In [1]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.impute import KNNImputer
from sklearn.model_selection import train_test_split, KFold, StratifiedKFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.ensemble import RandomForestClassifier
import optuna
from sklearn.feature_selection import RFECV
from sklearn.linear_model import LogisticRegressionCV
import joblib
import catboost

/Users/prathmesh/asep_project/venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Load both datasets
original = pd.read_csv("PCOS_data.csv")
new = pd.read_csv("pcos_dataset.csv")

# Set max columns to show is unlimited
pd.set_option('display.max_columns', None)

In [3]:
def preprocess(df):
    df = df.copy()  # avoid SettingWithCopyWarning

    # 1. Clean column names
    df.columns = df.columns.str.strip() \
                           .str.replace(' ', '_') \
                           .str.replace('(', '') \
                           .str.replace(')', '') \
                           .str.replace('.', '') \
                           .str.replace('-', '_') \
                           .str.replace('/', '_')
    df.rename(columns={'II____beta_HCGmIU_mL': 'II_beta_HCG'}, inplace=True)

    # 2. Drop irrelevant columns
    df.drop(columns=['Sl_No', 'Patient_File_No'], inplace=True, errors='ignore')
    df = df.loc[:, ~df.columns.str.startswith('Unnamed')]

    # 3. Merge Age columns
    if 'Age' not in df.columns and 'Age_yrs' in df.columns:
        df.rename(columns={'Age_yrs': 'Age'}, inplace=True)
    elif 'Age' in df.columns and 'Age_yrs' in df.columns:
        df['Age'] = df['Age'].fillna(df['Age_yrs'])
        df.drop(columns=['Age_yrs'], inplace=True)

    # 4. Merge PCOS diagnosis columns
    if 'PCOS_Diagnosis' in df.columns:
        df.rename(columns={'PCOS_Diagnosis': 'PCOS_Y_N'}, inplace=True)

    # 5. Handle missing values
    if 'Marraige_Status_Yrs' in df.columns:
        df.loc[:, 'Marraige_Status_Yrs'] = df['Marraige_Status_Yrs'].fillna(df['Marraige_Status_Yrs'].median())

    if 'Fast_food_Y_N' not in df.columns and 'Fast_food_YN' in df.columns:
        df.rename(columns={'Fast_food_YN': 'Fast_food_Y_N'}, inplace=True)
    if 'Fast_food_Y_N' in df.columns:
        df.loc[:, 'Fast_food_Y_N'] = df['Fast_food_Y_N'].fillna(df['Fast_food_Y_N'].mode()[0])

    # 6. Convert to numeric and fill missing values
    if 'II_beta_HCG' not in df.columns and 'II_beta_HCGmIU_mL' in df.columns:
        df.rename(columns={'II_beta_HCGmIU_mL': 'II_beta_HCG'}, inplace=True)
    if 'II_beta_HCG' in df.columns:
        df.loc[:, 'II_beta_HCG'] = pd.to_numeric(df['II_beta_HCG'], errors='coerce')
        df['II_beta_HCG'] = df['II_beta_HCG'].astype(float)
        df.loc[:, 'II_beta_HCG'] = df['II_beta_HCG'].fillna(df['II_beta_HCG'].median())

    if 'AMHng_mL' in df.columns:
        df.loc[:, 'AMHng_mL'] = pd.to_numeric(df['AMHng_mL'], errors='coerce')
        df['AMHng_mL'] = df['AMHng_mL'].astype(float)
        df.loc[:, 'AMHng_mL'] = df['AMHng_mL'].fillna(df['AMHng_mL'].median())

    return df

In [4]:
# Apply preprocessing
original_clean = preprocess(original)
new_clean = preprocess(new)

# Ensure consistent columns across both
all_columns = list(set(original_clean.columns).union(set(new_clean.columns)))

# Align both dataframes to same columns, fill missing with NaN
original_aligned = original_clean.reindex(columns=all_columns)
new_aligned = new_clean.reindex(columns=all_columns)

# Concatenate datasets
combined_df = pd.concat([original_aligned, new_aligned], ignore_index=True)

In [5]:
# Separate features and target
# X = combined_df.drop(columns=['PCOS_Y_N'])
X = combined_df.drop(columns=['PCOS_Y_N'])
y = combined_df['PCOS_Y_N']

# Initialize KNNImputer (e.g., with 5 nearest neighbors)
knn_imputer = KNNImputer(n_neighbors=5)

X = pd.DataFrame(knn_imputer.fit_transform(X), columns=X.columns)

# Sanitize feature names
X.columns = [str(col).replace(' ', '_')
                        .replace('"', '')
                        .replace("'", '')
                        .replace('[', '')
                        .replace(']', '')
                        .replace('{', '')
                        .replace('}', '')
                        .replace(':', '')
                        .replace(',', '')
                        for col in X.columns]

In [6]:
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)
X = pd.DataFrame(X_scaled, columns=X.columns)

In [7]:
model = catboost.CatBoostClassifier()
rfecv = RFECV(estimator=model, step=2, cv=5, scoring='accuracy', n_jobs=-1, verbose=1)
rfecv.fit(X, y)
selected_mask = rfecv.support_
selected_features = X.columns[selected_mask]
X = X[selected_features]
print(selected_features, len(selected_features))

Fitting estimator with 44 features.
Learning rate set to 0.011262
0:	learn: 0.6828094	total: 56.7ms	remaining: 56.7s
1:	learn: 0.6699587	total: 60.2ms	remaining: 30s
2:	learn: 0.6565144	total: 64.8ms	remaining: 21.5s
3:	learn: 0.6439570	total: 69.4ms	remaining: 17.3s
4:	learn: 0.6297482	total: 72.3ms	remaining: 14.4s
5:	learn: 0.6160333	total: 77.1ms	remaining: 12.8s
6:	learn: 0.6042384	total: 79.8ms	remaining: 11.3s
7:	learn: 0.5925074	total: 82.6ms	remaining: 10.2s
8:	learn: 0.5814736	total: 85ms	remaining: 9.36s
9:	learn: 0.5691606	total: 87.7ms	remaining: 8.68s
10:	learn: 0.5574657	total: 89.9ms	remaining: 8.09s
11:	learn: 0.5445095	total: 92.1ms	remaining: 7.58s
12:	learn: 0.5311004	total: 95.3ms	remaining: 7.23s
13:	learn: 0.5204234	total: 98.3ms	remaining: 6.92s
14:	learn: 0.5102890	total: 101ms	remaining: 6.65s
15:	learn: 0.5017263	total: 105ms	remaining: 6.43s
16:	learn: 0.4948532	total: 107ms	remaining: 6.2s
17:	learn: 0.4872443	total: 110ms	remaining: 6.01s
18:	learn: 0.4791

In [8]:
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.15, stratify=y, shuffle=True, random_state=8)

In [9]:
from catboost import CatBoostClassifier, Pool

def objective(trial):
    # Define hyperparameters for CatBoost
    param = {
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3, log=True),
        "iterations": trial.suggest_int("iterations", 100, 1000),
        "depth": trial.suggest_int("depth", 3, 12),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "random_strength": trial.suggest_float("random_strength", 1e-3, 10.0, log=True),
        "l2_leaf_reg": trial.suggest_float("l2_leaf_reg", 1e-3, 10.0, log=True),
        "loss_function": "Logloss",
        "eval_metric": "Accuracy",
        "random_seed": 8,
        "verbose": 0
    }

    # Prepare data
    train_pool = Pool(x_train, y_train)
    valid_pool = Pool(x_test, y_test)

    # Train model
    model = CatBoostClassifier(**param)
    model.fit(train_pool, eval_set=valid_pool, early_stopping_rounds=30)

    # Predict
    preds = model.predict(valid_pool)
    acc = accuracy_score(y_test, preds)

    return 1.0 - acc  # Optuna minimizes, so lower is better


In [10]:
study = optuna.create_study(direction='minimize')  # Because we return 1 - accuracy
study.optimize(objective, n_trials=50)  # Try 50 combinations (or more!)

print("Best hyperparameters:")
print(study.best_params)

print("Best accuracy:")
print(1 - study.best_value)

[I 2025-05-31 21:05:16,546] A new study created in memory with name: no-name-af67c10d-bd46-49e7-8de7-9d0559ba7174
[I 2025-05-31 21:05:16,677] Trial 0 finished with value: 0.025862068965517238 and parameters: {'learning_rate': 0.20086689682679262, 'iterations': 969, 'depth': 8, 'subsample': 0.8325490337848165, 'random_strength': 0.0667677175408411, 'l2_leaf_reg': 0.26297749054745234}. Best is trial 0 with value: 0.025862068965517238.
[I 2025-05-31 21:05:16,735] Trial 1 finished with value: 0.025862068965517238 and parameters: {'learning_rate': 0.029665636480832133, 'iterations': 542, 'depth': 4, 'subsample': 0.8495383042646973, 'random_strength': 0.03515546433476209, 'l2_leaf_reg': 0.007440064189302768}. Best is trial 0 with value: 0.025862068965517238.
[I 2025-05-31 21:05:16,798] Trial 2 finished with value: 0.017241379310344862 and parameters: {'learning_rate': 0.01179901469949373, 'iterations': 929, 'depth': 4, 'subsample': 0.6795069923955199, 'random_strength': 0.5000235854290613, '

Best hyperparameters:
{'learning_rate': 0.05745284059626672, 'iterations': 675, 'depth': 7, 'subsample': 0.7540284695790103, 'random_strength': 0.011489785028868103, 'l2_leaf_reg': 2.938057345620273}
Best accuracy:
0.9913793103448276


In [11]:
# Prepare data
train_pool = Pool(x_train, y_train)
valid_pool = Pool(x_test, y_test)

# Train model
best_model = CatBoostClassifier(**study.best_params)
best_model.fit(train_pool, eval_set=valid_pool, early_stopping_rounds=30)

# Predict
preds = best_model.predict(x_test)
preds = (preds > 0.5).astype(int)

# Compute final scores
acc = accuracy_score(y_test, preds)
precision = precision_score(y_test, preds, average='binary')
recall = recall_score(y_test, preds, average='binary')
f1 = f1_score(y_test, preds, average='binary')

print("\nFinal evaluation on test set:")
print(f"Accuracy: {acc * 100:.2f}")
print(f"Precision: {precision * 100:.2f}")
print(f"Recall: {recall * 100:.2f}")
print(f"F1 Score: {f1 * 100:.2f}")


0:	learn: 0.6155025	test: 0.6164606	best: 0.6164606 (0)	total: 1.78ms	remaining: 1.2s
1:	learn: 0.5492227	test: 0.5526466	best: 0.5526466 (1)	total: 4.17ms	remaining: 1.4s
2:	learn: 0.4859150	test: 0.4852918	best: 0.4852918 (2)	total: 7.45ms	remaining: 1.67s
3:	learn: 0.4291092	test: 0.4279180	best: 0.4279180 (3)	total: 9.38ms	remaining: 1.57s
4:	learn: 0.3857784	test: 0.3832250	best: 0.3832250 (4)	total: 11ms	remaining: 1.47s
5:	learn: 0.3537643	test: 0.3496749	best: 0.3496749 (5)	total: 12.7ms	remaining: 1.41s
6:	learn: 0.3178479	test: 0.3115830	best: 0.3115830 (6)	total: 14.4ms	remaining: 1.37s
7:	learn: 0.2909361	test: 0.2832492	best: 0.2832492 (7)	total: 15.9ms	remaining: 1.33s
8:	learn: 0.2670394	test: 0.2587631	best: 0.2587631 (8)	total: 17.6ms	remaining: 1.3s
9:	learn: 0.2474732	test: 0.2406547	best: 0.2406547 (9)	total: 19.2ms	remaining: 1.28s
10:	learn: 0.2303022	test: 0.2250017	best: 0.2250017 (10)	total: 21.1ms	remaining: 1.28s
11:	learn: 0.2172513	test: 0.2121672	best: 0.2